In [ ]:
#https://arxiv.org/pdf/1306.2597.pdf 46 col description


In [1]:
#https://github.com/dmlc/xgboost/tree/master/demo/rank from XGBoost github
#docs say they need lambda rank but only implemented pairwise rank ??
import xgboost as xgb
from xgboost import DMatrix
from sklearn.datasets import load_svmlight_file
import pandas as pd
import os
os.getcwd()

'/Users/dougchang/TDS/XGBoost'

In [2]:
#missing qid?
num=0
total=0
ids={}
with open('rank/mq2008.train','r') as fh: 
    for row in fh:
        #print(row)
        total+=1
        tok = row.split()
        if tok[0].strip()!='0':
            #print(row)
            if tok[0].strip() in ids:
                ids[tok[0].strip()]=ids[tok[0].strip()]+1
            else:
                ids[tok[0].strip()]=1
            num+=1
        #else:
        #    print('tok[0]:',tok[0])
        #print('tok[1]:',tok[1],tok[1].split(':')[1])
print('num:',num)
print('total:',total)
print('ids:',ids)

num: 1810
total: 9630
ids: {'2': 587, '1': 1223}


In [4]:
#missing qid?
num=0
total=0
ids={}
with open('rank/mq2008.train','r') as fh: 
    for row in fh:
        #print(row)
        total+=1
        tok = row.split()
        if tok[0].strip()!='0':
            #print(row)
            if tok[0].strip() in ids:
                ids[tok[0].strip()]=ids[tok[0].strip()]+1
            else:
                ids[tok[0].strip()]=1
            num+=1

print('num:',num)
print('total:',total)
print('ids:',ids) #there are only 2 ids, 1 and 2. and 0. This is for ? relevancy score? These aren't query ids. 

num: 1810
total: 9630
ids: {'2': 587, '1': 1223}


In [86]:
x_train, y_train = load_svmlight_file("rank/mq2008.train")
x_valid, y_valid = load_svmlight_file("rank/mq2008.vali")
x_test, y_test = load_svmlight_file("rank/mq2008.test")

print(type(x_train))

group_train = []
with open("rank/mq2008.train.group", "r") as f:
    data = f.readlines()
    for line in data:
        group_train.append(int(line.split("\n")[0]))

group_valid = []
with open("rank/mq2008.vali.group", "r") as f:
    data = f.readlines()
    for line in data:
        group_valid.append(int(line.split("\n")[0]))

group_test = []
with open("rank/mq2008.test.group", "r") as f:
    data = f.readlines()
    for line in data:
        group_test.append(int(line.split("\n")[0]))


<class 'scipy.sparse.csr.csr_matrix'>


In [87]:
total=0
with open('rank/mq2008.train.group', 'r') as fh:
    n = fh.readlines()
    for line in n:
        total+=int(line.strip())
print(total)

9630


In [88]:
train_dmatrix = DMatrix(x_train, y_train)
valid_dmatrix = DMatrix(x_valid, y_valid)
test_dmatrix = DMatrix(x_test)

train_dmatrix.set_group(group_train)
valid_dmatrix.set_group(group_valid)



params = {'objective': 'rank:pairwise', 'eta': 0.1, 'gamma': 1.0,
               'min_child_weight': 0.1, 'max_depth': 6}
xgb_model = xgb.train(params, train_dmatrix, num_boost_round=4,
                           evals=[(valid_dmatrix, 'validation')])
pred = xgb_model.predict(test_dmatrix)

[0]	validation-map:0.70901
[1]	validation-map:0.731518
[2]	validation-map:0.739957
[3]	validation-map:0.743337


In [92]:
from scipy.stats import spearmanr
print(y_test.shape,pred.shape)
print(spearmanr(y_test, pred))

print(pred)

(2874,) (2874,)
SpearmanrResult(correlation=0.36215681044800113, pvalue=8.555306021538603e-90)
[0.6176246  0.2126602  0.6080335  ... 0.46931526 0.7187472  0.28511757]


In [99]:
params = {'objective': 'rank:pairwise', 'learning_rate': 0.1,
          'gamma': 1.0, 'min_child_weight': 0.1,
          'max_depth': 6, 'n_estimators': 4}
model = xgb.sklearn.XGBRanker(**params)
model.fit(x_train, y_train, group_train,
          eval_set=[(x_valid, y_valid)], eval_group=[group_valid])
pred = model.predict(x_train)
#pred_test = model.predict(y_test)
#print(spearmanr(y_test, pred_test))
print(spearmanr(y_train, pred))



SpearmanrResult(correlation=0.44876790183974274, pvalue=0.0)


In [ ]:
print(len(pred))

In [96]:
import lightgbm as lgb

gbm = lgb.LGBMRanker()
gbm.fit(x_train, y_train, group=group_train, eval_set=[(x_valid, y_valid)],
eval_group=[group_valid], eval_at=[1, 3], early_stopping_rounds=20, verbose=True,
callbacks=[lgb.reset_parameter(learning_rate=lambda x: 0.95 ** x * 0.1)])

[1]	valid_0's ndcg@1: 0.556263	valid_0's ndcg@3: 0.635254
Training until validation scores don't improve for 20 rounds.
[2]	valid_0's ndcg@1: 0.571125	valid_0's ndcg@3: 0.66308
[3]	valid_0's ndcg@1: 0.617834	valid_0's ndcg@3: 0.675826
[4]	valid_0's ndcg@1: 0.622081	valid_0's ndcg@3: 0.682879
[5]	valid_0's ndcg@1: 0.632696	valid_0's ndcg@3: 0.6769
[6]	valid_0's ndcg@1: 0.624204	valid_0's ndcg@3: 0.677868
[7]	valid_0's ndcg@1: 0.613588	valid_0's ndcg@3: 0.671651
[8]	valid_0's ndcg@1: 0.613588	valid_0's ndcg@3: 0.670299
[9]	valid_0's ndcg@1: 0.626327	valid_0's ndcg@3: 0.675637
[10]	valid_0's ndcg@1: 0.62845	valid_0's ndcg@3: 0.680989
[11]	valid_0's ndcg@1: 0.62845	valid_0's ndcg@3: 0.679431
[12]	valid_0's ndcg@1: 0.626327	valid_0's ndcg@3: 0.684499
[13]	valid_0's ndcg@1: 0.641189	valid_0's ndcg@3: 0.688833
[14]	valid_0's ndcg@1: 0.619958	valid_0's ndcg@3: 0.688054
[15]	valid_0's ndcg@1: 0.619958	valid_0's ndcg@3: 0.686626
[16]	valid_0's ndcg@1: 0.626327	valid_0's ndcg@3: 0.691959
[17]	val

LGBMRanker(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
           importance_type='split', learning_rate=0.1, max_depth=-1,
           min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
           n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
           random_state=None, reg_alpha=0.0, reg_lambda=0.0, silent=True,
           subsample=1.0, subsample_for_bin=200000, subsample_freq=0)

In [97]:
preds_train = gbm.predict(x_train)
spearmanr(y_train, preds_train)

SpearmanrResult(correlation=0.41298395158905504, pvalue=0.0)

In [9]:
type(preds_train)

NameError: name 'preds_train' is not defined

In [105]:
print(spearmanr([1,2,3],[5,7,9])) #both increasing

print(spearmanr([1,2,3],[7,5,3])) #one increasing, one decreasing
print(spearmanr([10,8,4],[11,3,6])) #both decreasing

SpearmanrResult(correlation=1.0, pvalue=0.0)
SpearmanrResult(correlation=-1.0, pvalue=0.0)
SpearmanrResult(correlation=0.5, pvalue=0.6666666666666667)


In [8]:
import sys

gr=[]
num=0


with open ('rank/mq2008.train.group','r') as fh:
    lines = fh.readlines()
    for l in lines:
        gr.append(int(l.strip()))
        num+=1
print('num_groups:',num)

data=[]
num=0
with open('rank/train.txt','r') as fh:
    lines = fh.readlines()
    for line in lines:
        #print(line.strip())
        #print('--------------')
        data.append(line.strip())
        num+=1

probs ={}
def get_prob(line):
    return float(line[line.find('prob ='):].split('=')[1])
for x in range(len(data)):
    #print(get_prob(data[x]))
    probs[x]=get_prob(data[x])
#print (probs)
print('num:',num)
ds = {}
last_seen = 0
#what do we want? print probs for all groups? and rank them? if there are 8 lines in a group then 
#print them sorted? 
for idx_gr in gr:
    print("idx_gr:",idx_gr)
    sort_prob=[]
    for x in range(last_seen,last_seen+idx_gr):
        print(data[x])
        sort_prob.append(probs[x])
        print('-----------')
    print(sort_prob)
    print(sorted(sort_prob))
    
    for idx in range(len(sorted(sort_prob))):
        print('processing:',sorted(sort_prob)[idx],":",sort_prob.index(sorted(sort_prob)[idx]))
    last_seen = last_seen+idx_gr
    

num_groups: 471
num: 9630
idx_gr: 8
0 qid:10002 1:0.007477 2:0.000000 3:1.000000 4:0.000000 5:0.007470 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.471076 12:0.000000 13:1.000000 14:0.000000 15:0.477541 16:0.005120 17:0.000000 18:0.571429 19:0.000000 20:0.004806 21:0.768561 22:0.727734 23:0.716277 24:0.582061 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.780495 30:0.962382 31:0.999274 32:0.961524 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.797056 38:0.697327 39:0.721953 40:0.582568 41:0.000000 42:0.000000 43:0.000000 44:0.000000 45:0.000000 46:0.007042 #docid = GX008-86-4444840 inc = 1 prob = 0.086622
-----------
0 qid:10002 1:0.603738 2:0.000000 3:1.000000 4:0.000000 5:0.603175 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.000000 12:0.000000 13:0.122130 14:0.000000 15:0.000000 16:0.998377 17:0.375000 18:1.000000 19:0.000000 20:0.998128 21:0.000000 22:0.000000 23:0.154578 24:0.555676 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.071

processing: 0.129212 : 29
processing: 0.129612 : 24
processing: 0.132397 : 12
processing: 0.143665 : 25
processing: 0.14995 : 5
processing: 0.179385 : 10
processing: 0.180675 : 8
processing: 0.182968 : 3
processing: 0.189822 : 27
processing: 0.191264 : 6
processing: 0.193221 : 18
processing: 0.195695 : 26
processing: 0.20352 : 22
processing: 0.434913 : 21
processing: 0.466902 : 20
num: []
idx_gr: 8
0 qid:10197 1:0.045198 2:1.000000 3:1.000000 4:0.000000 5:0.056180 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.042680 12:1.000000 13:1.000000 14:0.000000 15:0.053686 16:0.181063 17:0.625000 18:1.000000 19:0.000000 20:0.180594 21:0.098921 22:0.330037 23:0.570489 24:0.346145 25:0.604661 26:0.000000 27:0.000000 28:0.000000 29:0.694922 30:0.000000 31:0.000000 32:0.000000 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.211223 38:0.356046 39:0.629185 40:0.370274 41:0.250000 42:0.000000 43:0.000000 44:0.551605 45:0.060606 46:1.000000 #docid = GX002-80-3104818 inc = 0.001659856

-----------
0 qid:10419 1:0.096712 2:0.000000 3:0.500000 4:0.000000 5:0.096455 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.143634 12:0.000000 13:0.150629 14:0.000000 15:0.144921 16:0.118607 17:0.043478 18:0.440000 19:0.150000 20:0.118804 21:0.214488 22:0.515860 23:0.631429 24:0.621815 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.090821 30:0.000000 31:0.000000 32:0.000000 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.206352 38:0.524592 39:0.633441 40:0.627637 41:0.500000 42:0.348837 43:0.000000 44:0.004208 45:0.007299 46:0.000000 #docid = GX009-82-4233962 inc = 1 prob = 0.0900028
-----------
0 qid:10419 1:0.017555 2:0.000000 3:0.000000 4:0.000000 5:0.016927 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.159763 12:0.000000 13:0.000000 14:0.000000 15:0.161490 16:0.018296 17:0.326087 18:0.760000 19:0.200000 20:0.018934 21:0.190256 22:0.274380 23:0.215063 24:0.337198 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.000000 30:0.000000 31:0.00

processing: 0.53732 : 2
processing: 0.572251 : 19
processing: 0.584838 : 23
processing: 0.597226 : 14
num: []
idx_gr: 8
0 qid:10652 1:0.124936 2:1.000000 3:1.000000 4:0.000000 5:0.127506 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.681528 12:1.000000 13:0.455292 14:0.000000 15:0.682831 16:0.093357 17:1.000000 18:1.000000 19:0.400000 20:0.095173 21:0.648515 22:0.923606 23:0.932495 24:0.969029 25:0.148070 26:0.000000 27:0.000000 28:0.000000 29:0.272014 30:0.285499 31:0.116890 32:0.346808 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.657142 38:0.926393 39:0.927669 40:0.971501 41:0.250000 42:0.103448 43:0.000000 44:1.000000 45:1.000000 46:1.000000 #docid = GX006-18-9104016 inc = 0.0179110481588457 prob = 0.136424
-----------
0 qid:10652 1:0.027249 2:0.000000 3:0.000000 4:0.000000 5:0.026221 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.770424 12:0.000000 13:0.000000 14:0.000000 15:0.774629 16:0.018277 17:0.209677 18:0.272727 19:0.800000 20:0.018567 21:

processing: 0.142786 : 21
processing: 0.153419 : 20
processing: 0.157183 : 25
processing: 0.16105 : 22
processing: 0.175717 : 8
processing: 0.206042 : 13
processing: 0.267764 : 29
processing: 0.294989 : 11
processing: 0.303201 : 10
processing: 0.321581 : 7
num: []
idx_gr: 31
1 qid:10800 1:0.194595 2:0.000000 3:0.000000 4:0.000000 5:0.193626 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.153938 12:0.000000 13:0.000000 14:0.000000 15:0.148380 16:0.181130 17:0.111111 18:0.111111 19:0.125000 20:0.181221 21:0.251885 22:0.454451 23:0.546375 24:0.505770 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.000000 30:0.000000 31:0.000000 32:0.000000 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.250674 38:0.454726 39:0.547931 40:0.504265 41:0.000000 42:0.076923 43:0.000000 44:0.257024 45:0.073684 46:0.000000 #docid = GX001-39-4370345 inc = 1 prob = 0.0897452
-----------
0 qid:10800 1:0.010210 2:0.000000 3:0.000000 4:0.000000 5:0.009020 6:0.000000 7:0.000000 8:0.000000 9:0.00

...

processing: 0.160706 : 70
processing: 0.178951 : 34
processing: 0.180644 : 62
processing: 0.181886 : 29
processing: 0.194138 : 106
processing: 0.197009 : 20
processing: 0.204376 : 76
processing: 0.207655 : 103
processing: 0.20783 : 24
processing: 0.211059 : 13
processing: 0.216256 : 66
processing: 0.225008 : 32
processing: 0.229758 : 27
processing: 0.242519 : 26
processing: 0.263027 : 30
num: []
idx_gr: 16
0 qid:14923 1:0.171935 2:0.000000 3:0.000000 4:0.000000 5:0.171670 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.599676 12:0.000000 13:0.000000 14:0.000000 15:0.602764 16:0.179723 17:0.555556 18:0.777778 19:0.176471 20:0.179910 21:0.096022 22:0.533725 23:0.610785 24:0.561450 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.000000 30:0.000000 31:0.000000 32:0.000000 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.100209 38:0.540942 39:0.612708 40:0.570381 41:0.200000 42:0.086207 43:0.000000 44:0.332428 45:1.000000 46:1.000000 #docid = GX000-14-11865508 inc = 1 

processing: 0.0892206 : 7
processing: 0.0894455 : 6
processing: 0.0895707 : 24
processing: 0.0896912 : 12
processing: 0.089745 : 22
processing: 0.0897452 : 0
processing: 0.0897452 : 0
processing: 0.0899126 : 29
processing: 0.0899627 : 26
processing: 0.0910526 : 23
processing: 0.0911546 : 14
processing: 0.091734 : 19
processing: 0.0929851 : 21
processing: 0.0940304 : 5
processing: 0.0977312 : 20
processing: 0.102538 : 9
processing: 0.105656 : 27
processing: 0.108882 : 3
processing: 0.109712 : 10
processing: 0.115334 : 8
processing: 0.13104 : 4
processing: 0.13156 : 25
processing: 0.134038 : 2
processing: 0.139356 : 28
processing: 0.140942 : 30
processing: 0.274894 : 17
num: []
idx_gr: 16
0 qid:15221 1:0.031764 2:0.000000 3:0.000000 4:0.000000 5:0.030940 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.967324 12:0.000000 13:0.000000 14:0.000000 15:0.963415 16:0.017351 17:0.142857 18:0.200000 19:0.041667 20:0.017352 21:0.701958 22:0.614451 23:0.857518 24:0.729715 25:0.000000 2

processing: 0.0898356 : 5
processing: 0.0909676 : 7
processing: 0.106955 : 2
processing: 0.219911 : 6
num: []
idx_gr: 8
0 qid:15563 1:0.760383 2:0.000000 3:1.000000 4:0.000000 5:0.766773 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.738652 12:0.000000 13:1.000000 14:0.000000 15:0.744849 16:0.882664 17:0.000000 18:1.000000 19:0.666667 20:0.883225 21:0.526824 22:0.150130 23:0.216585 24:0.139735 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:1.000000 30:1.000000 31:1.000000 32:1.000000 33:0.000000 34:0.000000 35:0.000000 36:0.000000 37:0.555172 38:0.158469 39:0.222984 40:0.148936 41:0.666667 42:1.000000 43:0.000000 44:0.000000 45:0.000000 46:0.000000 #docid = GX003-53-7262718 inc = 0.00140974468100401 prob = 0.0897976
-----------
0 qid:15563 1:0.246006 2:1.000000 3:0.000000 4:0.000000 5:0.252396 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.142911 12:1.000000 13:0.000000 14:0.000000 15:0.143305 16:0.005495 17:1.000000 18:0.250000 19:0.333333 20:0.005681 2

processing: 0.824826 : 2
processing: 0.833999 : 6
processing: 0.958565 : 5
num: []
idx_gr: 16
2 qid:15764 1:1.000000 2:0.000000 3:0.500000 4:0.500000 5:1.000000 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:1.000000 12:0.000000 13:0.426023 14:0.360793 15:1.000000 16:0.042937 17:0.170213 18:0.625000 19:0.500000 20:0.043222 21:0.943508 22:0.892336 23:1.000000 24:0.890659 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.214693 30:0.000000 31:0.000000 32:0.000000 33:0.317471 34:0.209667 35:0.146021 36:0.170732 37:0.926140 38:0.882951 39:1.000000 40:0.882501 41:0.750000 42:0.585366 43:0.000000 44:0.000495 45:0.001383 46:1.000000 #docid = GX000-48-6476344 inc = 1 prob = 0.585273
-----------
2 qid:15764 1:0.240343 2:1.000000 3:0.500000 4:0.000000 5:0.280851 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.193782 12:1.000000 13:0.426023 14:0.000000 15:0.288401 16:0.015917 17:0.808511 18:0.500000 19:0.375000 20:0.016843 21:0.798067 22:0.779841 23:0.673436 24:0.79420

processing: 0.120789 : 99
processing: 0.122599 : 103
processing: 0.123241 : 114
processing: 0.124705 : 95
processing: 0.127174 : 51
processing: 0.135938 : 27
processing: 0.136564 : 87
processing: 0.139548 : 57
processing: 0.143099 : 89
processing: 0.144534 : 53
processing: 0.144844 : 84
processing: 0.148437 : 6
processing: 0.151924 : 15
processing: 0.154258 : 88
processing: 0.158798 : 92
processing: 0.165828 : 45
processing: 0.167991 : 86
processing: 0.173387 : 54
processing: 0.174629 : 90
processing: 0.176849 : 21
processing: 0.177431 : 112
processing: 0.183354 : 22
processing: 0.28242 : 41
num: []
idx_gr: 15
0 qid:15917 1:0.179567 2:0.000000 3:0.000000 4:0.000000 5:0.174455 6:0.000000 7:0.000000 8:0.000000 9:0.000000 10:0.000000 11:0.000000 12:0.000000 13:0.000000 14:0.000000 15:0.000000 16:0.122639 17:0.857143 18:0.400000 19:0.000000 20:0.123170 21:0.132383 22:0.430077 23:0.556585 24:0.576651 25:0.000000 26:0.000000 27:0.000000 28:0.000000 29:0.000000 30:0.000000 31:0.000000 32:0.00

In [167]:
data[0]
data[0][2:(len(data[0])-2)]
#data[0][2:(len(data[0])-2)].find('prob =')
data[0].find('prob =')
float(data[0][data[0].find('prob ='):].split('=')[1])#gets probability for each query, then can rank the probabilities
#removing the leading 0 and the \n at end
#len(data)
probs ={}
def get_prob(line):
    return float(line[line.find('prob ='):].split('=')[1])
for x in range(len(data)):
    #print(get_prob(data[x]))
    probs[x]=get_prob(data[x])
print (probs)

{0: 0.086622, 1: 0.0897452, 2: 0.0999735, 3: 0.0444806, 4: 0.0410162, 5: 0.114018, 6: 0.133097, 7: 0.111686, 8: 0.0892077, 9: 0.0894792, 10: 0.0825829, 11: 0.139842, 12: 0.341364, 13: 0.0701303, 14: 0.400738, 15: 0.0911017, 16: 0.260843, 17: 0.0369378, 18: 0.119188, 19: 0.115017, 20: 0.0897079, 21: 0.0895514, 22: 0.211328, 23: 0.0898218, 24: 0.0171166, 25: 0.0694043, 26: 0.637585, 27: 0.107073, 28: 0.135084, 29: 0.790266, 30: 0.495703, 31: 0.169748, 32: 0.352855, 33: 0.266764, 34: 0.0899239, 35: 0.0647587, 36: 0.076647, 37: 0.0964041, 38: 0.0903421, 39: 0.189357, 40: 0.0897452, 41: 0.978707, 42: 0.0465332, 43: 0.867248, 44: 0.983119, 45: 0.0830865, 46: 0.392123, 47: 0.505019, 48: 0.269895, 49: 0.779311, 50: 0.286562, 51: 0.967445, 52: 0.10788, 53: 0.0615237, 54: 0.106378, 55: 0.121025, 56: 0.0115498, 57: 0.0897452, 58: 0.0957367, 59: 0.172174, 60: 0.317664, 61: 0.0953978, 62: 0.249609, 63: 0.297692, 64: 0.0897452, 65: 0.0897452, 66: 0.0897452, 67: 0.080043, 68: 0.0897452, 69: 0.0888186

<h5>Ranking metrics</h5>
<p>Notation: 2 inputs, $doc_i$ is the document where i is the number of the document, $rel(i)$ is the relevancy score and
$D(i)$ is the discount factor, $G(i)$ is the gain for each document. The objective is to create a function
which captures both the individual relevance score per document and the position of a document. A relevant document
ranked at the top should have a higher score than the same document one position below. To do this we compose a function
with 2 subfunctions. 
</p>
<p>Define a 3 value relevancy score where 1) not relevant, 2) partially
relevant, 3) completely relevant. This scale can be adusted. The wiki page uses 0 as a relevancy score. I removed 
this because most relevancy scales in the papers do not include 0 as being the most irrelevant or relevant score. 
Relevancy is a fixed discrete integer. Zero is not always a good idea because it removes the effect of any equation and may not preserve the same scaling factors
as for the other integers. 
</p>
<p>Cumulative Gain</p>
$CG=\sum_{doc(i)}^N rel=3+2+3+0+1+2=11$
<p></p>
The problem with CG is it does not take into account the position of the query result. We can multiply the
relevancy with some factor to account for the position. We want the overall scale to be higher the higher the document
is so that implies a divide by a shrinking number as the document gets to a lower position. Take the log of the position to scale
the result and to keep it smooth and bounded. Add 1 to prevent 0 entry; if the first position is defined as 0. 
<p>DCG, Discounted Cumulative Gain</p>
There are multiple definitions for DCG. DCG is the product of the discount factor and gain factor. The 
$DCG=\sum_{doc(i)}^{N}G(i)D(i)$
<p>Gain</p>
$G(i)=2^{rel_i-1}$ or $G(i)=rel_i$ 
<p>There are 2 definitions of gain, one which uses the exponential factor above or another which uses
the relevance score only. </p>
<p>Discount</p>
$D(pos(i))=\frac{1}{log_{2}(1+pos(i))}$
<p>where pos(i) is the position number of the document. The table from wiki uses i as pos(i) </p>
<p>NDCG, Normalized Discounted Cumulative Gain</p>
The problem with the above metric is longer search results have higher scores. Normalize using the discount defined above
where a higher position for a document means a higher score. The NDCG score in the table below uses the relevance
score as the gain, $NDCG= 3+1.26+1.5+0+.387+.712=6.86$
<img src="images/DCG.png"/>
